In [2]:
import pandas as pd

import os

import numpy as np
import xarray as xr
import pandas as pd
import matplotlib.pyplot as plt
from allensdk.brain_observatory.ecephys.ecephys_project_cache import EcephysProjectCache
from allensdk.brain_observatory.ecephys.align_timestamps.barcode_sync_dataset import BarcodeSyncDataset
from allensdk.brain_observatory.ecephys.align_timestamps.probe_synchronizer import ProbeSynchronizer
from allensdk.brain_observatory.ecephys.align_timestamps import barcode
from allensdk.brain_observatory.ecephys.align_timestamps.channel_states import extract_barcodes_from_states, extract_splits_from_states

In [24]:
df = pd.read_csv('/alzheimer/Noam/9598406/Allen/allen_wt_sessions.csv', index_col=0)

'/alzheimer/Noam/9598406/Allen/data/session_732592105'

In [25]:
for sesi in range(len(df)):
    
    ses_path = df.session_name[sesi]
    probe_path = df.probe_name[sesi]
    
    sync_dataset = BarcodeSyncDataset.factory(ses_path +  '/sync.h5')
    sync_times, sync_codes = sync_dataset.extract_barcodes() 
    
    sampling_rate = df.sampling_frequency[sesi]

    channel_states = np.load(probe_path + '/channel_states.npy')
    timestamps     = np.load(probe_path + '/event_timestamps.npy')

    probe_barcode_times, probe_barcodes = extract_barcodes_from_states(
        channel_states, timestamps, sampling_rate
    )
    probe_split_times = extract_splits_from_states(
        channel_states, timestamps, sampling_rate
    )
    
    synchronizers = []
    

    for idx, split_time in enumerate(probe_split_times):

        min_time = probe_split_times[idx]

        if idx == (len(probe_split_times) - 1):
            max_time = np.Inf
        else:
            max_time = probe_split_times[idx + 1]

        synchronizer = ProbeSynchronizer.compute(
            sync_times,
            sync_codes,
            probe_barcode_times,
            probe_barcodes,
            min_time,
            max_time,
            0,
            sampling_rate,
        )

        synchronizers.append(synchronizer)
        
        if len(synchronizers) == 1: 
            timelag = synchronizers[0].total_time_shift
        else:
            timelag = np.zeros([2,len(synchronizers)])
            for inx in range(len(synchronizers)):
                timelag[0,inx] = synchronizers[inx].total_time_shift
                timelag[1,inx] = synchronizers[inx].min_time

        #print(timelag)
        
        np.save(probe_path + '/probe_lags.npy', timelag)


Num barcodes: 303
Master start index: [0]
Probe end index: -2
total_time_shift: [-0.53783511]
Num barcodes: 310
Master start index: [1]
Probe end index: -1
total_time_shift: [-3.7405169]
Num barcodes: 314
Master start index: [0]
Probe end index: -2
total_time_shift: [-3.78750046]
Num barcodes: 319
Master start index: [0]
Probe end index: -1
total_time_shift: [-3.75690541]
Num barcodes: 312
Master start index: [0]
Probe end index: -2
total_time_shift: [-3.69516082]
Num barcodes: 312
Master start index: [0]
Probe end index: -2
total_time_shift: [-3.8109754]
Num barcodes: 310
Master start index: [0]
Probe end index: -2
total_time_shift: [-3.7445548]
Num barcodes: 311
Master start index: [0]
Probe end index: -1
total_time_shift: [-3.72753468]
Num barcodes: 311
Master start index: [0]
Probe end index: -1
total_time_shift: [-3.79763074]
Num barcodes: 329
Master start index: [0]
Probe end index: -2
total_time_shift: [-3.72929501]
Num barcodes: 316
Master start index: [0]
Probe end index: -1
t